In [1]:
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import warnings
warnings.filterwarnings('ignore')
os.environ["CUDA_DEVICE_ORDER"] = "PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]="0"
import pandas as pd
import numpy as np
from gtda.time_series import SlidingWindow
import matplotlib.pyplot as plt
from tensorflow.python.keras.backend import set_session
import tensorflow as tf
config = tf.compat.v1.ConfigProto() 
config.gpu_options.allow_growth = True  
config.log_device_placement = True  
sess2 = tf.compat.v1.Session(config=config)
set_session(sess2)  
from tensorflow.keras.layers import Dense, MaxPooling1D, Flatten
from tensorflow.keras import Input, Model
from tensorflow.keras.callbacks import ModelCheckpoint
import tensorflow.compat.v1.keras.backend as K
from tensorflow.keras.models import load_model
from tcn import TCN, tcn_full_summary
from tcn import compiled_tcn
from tensorflow.keras.utils import to_categorical
import csv
import random
import itertools
from keras_flops import get_flops
from mango.tuner import Tuner
import time
from tensorflow.keras.losses import MSE
import pickle
from hardware_utils import *
from data_utils import *

Device mapping:
/job:localhost/replica:0/task:0/device:GPU:0 -> device: 0, name: NVIDIA GeForce RTX 3090, pci bus id: 0000:01:00.0, compute capability: 8.6



In [2]:
sampling_rate = 100
window_size = 550
stride = 50
epsilon = 0.4
f = '/home/nesl/earable/Earable/Activity_Dataset/' #dataset directory

X_tr, Y_tr, X_test, Y_test = import_auritus_activity_dataset(dataset_folder = f, 
                                use_timestamp=False, 
                                shuffle=True, 
                                window_size = window_size, stride = stride, 
                                return_test_set = True, test_set_size = 300,channels=0)


random_indices = np.random.choice(X_tr.shape[0], size=1000, replace=False)
X_val = X_tr[random_indices,:,:]
Y_val = Y_tr[random_indices,:]
X_tr = np.delete(X_tr,random_indices,axis=0)
Y_tr = np.delete(Y_tr,random_indices,axis=0)

print(X_tr.shape)
print(Y_tr.shape)
print(X_val.shape)
print(Y_val.shape)
print(X_test.shape)
print(Y_test.shape)

100%|█████████████████████████████████████████| 399/399 [00:11<00:00, 34.62it/s]


(13671, 550, 6)
(13671, 9)
(1000, 550, 6)
(1000, 9)
(300, 550, 6)
(300, 9)


In [3]:
def fgsm_attack(model, image, label, eps):
    image = tf.cast(image, tf.float32)
    with tf.GradientTape() as tape:
        tape.watch(image)
        pred = model(image)
        loss = MSE(label, pred)
        gradient = tape.gradient(loss, image)
        signedGrad = tf.sign(gradient)
        adversary = (image + (signedGrad * eps)).numpy()
        return adversary
    
def perform_fgsm_attack(data,lab,eps,my_model):
    countadv = 0
    for i in tqdm(range(len(data))):
        act = data[i,:,:].reshape(1,data.shape[1],data.shape[2])
        label = lab[i,:]
        actPred = my_model.predict(act)
        actPred = actPred.argmax()
        adversary = fgsm_attack(my_model,act, label, eps=eps)
        pred = my_model.predict(adversary)
        adversaryPred = pred[0].argmax()
        if actPred == adversaryPred:
            countadv += 1
        
 
    adv_accu = countadv / len(data)
    return adv_accu

In [4]:
dirpath="/home/nesl/Mbed Programs/auritus_tcn/" #hardware program directory - this is where the TCN deployment code is stored
device = "NUCLEO_F746ZG" #which hardware to use
model_name = 'Auritus_noadv'+device+'.hdf5'
HIL = False #use real hardware or proxy?
quantization = False #use quantization or not?
model_epochs = 500 #epochs to train each model for
NAS_epochs = 50 #epochs for hyperparameter tuning
output_name = 'g_model_2.tflite'
log_file_name = 'TCN_Auritus_noadv_'+device+'.csv'
if os.path.exists(log_file_name):
    os.remove(log_file_name)
row_write = ['score', '1-accuracy','adv_accuracy','RAM','Flash','FLOPS','Latency','nb_filters','kernel_size',
             'dilations','use_skip_connections']
with open(log_file_name, 'a', newline='') as csvfile:
    csvwriter = csv.writer(csvfile)
    csvwriter.writerow(row_write)
if os.path.exists(log_file_name[0:-4]+'.p'):
    os.remove(log_file_name[0:-4]+'.p')

In [5]:
def objective_NN(epochs=1000,nb_filters=10,kernel_size=3,
                 dilations=[1, 2, 4, 8, 16, 32, 64, 128, 256],
                 use_skip_connections=True):
    
    err = 'inf'
    adv_accu = 'inf'
    input_dim=X_tr.shape[2]
    
    model = compiled_tcn(return_sequences=False,
                         num_feat=input_dim,
                         num_classes=Y_tr.shape[1],
                         nb_filters=nb_filters,
                         kernel_size=kernel_size,
                         dilations=dilations,
                         nb_stacks=1,
                         max_len=window_size,
                         use_weight_norm=False,
                         use_skip_connections=use_skip_connections)
    
    opt = tf.keras.optimizers.Adam()
    model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
                  optimizer=opt,metrics=['accuracy'])
    Flops = get_flops(model, batch_size=1)
    convert_to_tflite_model(model=model,training_data=X_tr,quantization=quantization,output_name=output_name) 
    maxRAM, maxFlash = return_hardware_specs(device)
    
    if(HIL==True):
        convert_to_cpp_model(dirpath)
        RAM, Flash, Latency, idealArenaSize, errorCode = HIL_controller(dirpath=dirpath,
                                                                       chosen_device=device,
                                                                       window_size=window_size, 
                                                                    number_of_channels = input_dim,
                                                                   quantization=quantization)     
        score = -5.0
        if(Flash==-1):
            row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
            print('Design choice:',row_write)
            with open(log_file_name, 'a', newline='') as csvfile:
                csvwriter = csv.writer(csvfile)
                csvwriter.writerow(row_write)
            return score    
    
        elif(Flash!=-1):
            checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
            model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
                      epochs=epochs,callbacks=[checkpoint],shuffle=True,verbose=1)
            err = 1-checkpoint.best
            #adv_accu = perform_fgsm_attack(data=X_val, lab=Y_val,eps=epsilon,my_model=model)
            
            resource_usage = (RAM/maxRAM) + (Flash/maxFlash) 
            score = -err + 0.01*resource_usage - 0.05*Latency #- (0.5*(1-adv_accu)) #weigh each component as you like
                
            row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
            print('Design choice:',row_write)
            with open(log_file_name, 'a', newline='') as csvfile:
                csvwriter = csv.writer(csvfile)
                csvwriter.writerow(row_write)   
    else:
        score = -5.0
        Flash = os.path.getsize(output_name)
        RAM = get_model_memory_usage(batch_size=1,model=model)
        Latency=-1
        max_flops = (30e6)
        
        if(RAM < maxRAM and Flash<maxFlash):
            checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
            model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
                      epochs=epochs,callbacks=[checkpoint],shuffle=True,verbose=1)
            err = 1-checkpoint.best 
            #adv_accu = perform_fgsm_attack(data=X_val, lab=Y_val,eps=epsilon,my_model=model)
            resource_usage = (RAM/maxRAM) + (Flash/maxFlash)
            score = -err + 0.01*resource_usage - 0.05*(Flops/max_flops)#- (0.5*(1-adv_accu))  #weigh each component as you like
        
        row_write = [score, err,adv_accu,RAM,Flash,Flops,Latency,
                 nb_filters,kernel_size,dilations,use_skip_connections]
        print('Design choice:',row_write)
        with open(log_file_name, 'a', newline='') as csvfile:
            csvwriter = csv.writer(csvfile)
            csvwriter.writerow(row_write) 
    
    return score        

In [6]:
import pickle 

def save_res(data, file_name):
    pickle.dump( data, open( file_name, "wb" ) )
    
min_layer = 3
max_layer = 8
a_list = [1,2,4,8,16,32,64,128,256]
all_combinations = []
dil_list = []
for r in range(len(a_list) + 1):
    combinations_object = itertools.combinations(a_list, r)
    combinations_list = list(combinations_object)
    all_combinations += combinations_list
all_combinations = all_combinations[1:]
for item in all_combinations:
    if(len(item) >= min_layer and len(item) <= max_layer):
        dil_list.append(list(item))

param_dict = {
    'nb_filters': range(2,64),
    'kernel_size': range(2,16),
    'use_skip_connections': [True, False],
    'dil_list': dil_list
}

def objfunc(args_list):

    objective_evaluated = []
    
    start_time = time.time()
    
    for hyper_par in args_list:
        nb_filters = hyper_par['nb_filters']
        kernel_size = hyper_par['kernel_size']
        use_skip_connections = hyper_par['use_skip_connections']
        dil_list = hyper_par['dil_list']
            
        objective = objective_NN(epochs=model_epochs,nb_filters=nb_filters,kernel_size=kernel_size,
                                 dilations=dil_list,use_skip_connections=use_skip_connections,)
        objective_evaluated.append(objective)
        
        end_time = time.time()
        print('objective:', objective, ' time:',end_time-start_time)
        
    return objective_evaluated

conf_Dict = dict()
conf_Dict['batch_size'] = 1 
conf_Dict['num_iteration'] = NAS_epochs
conf_Dict['initial_random']= 5
tuner = Tuner(param_dict, objfunc,conf_Dict)
all_runs = []
results = tuner.maximize()
all_runs.append(results)
save_res(all_runs,log_file_name[0:-4]+'.p')

x.shape= (None, 34)
model.x = (None, 550, 6)
model.y = (None, 9)
Instructions for updating:
Use `tf.compat.v1.graph_util.tensor_shape_from_node_def_name`

=========================Options=============================
-max_depth                  10000
-min_bytes                  0
-min_peak_bytes             0
-min_residual_bytes         0
-min_output_bytes           0
-min_micros                 0
-min_accelerator_micros     0
-min_cpu_micros             0
-min_params                 0
-min_float_ops              1
-min_occurrence             0
-step                       -1
-order_by                   float_ops
-account_type_regexes       .*
-start_name_regexes         .*
-trim_name_regexes          
-show_name_regexes          .*
-hide_name_regexes          
-account_displayed_op_only  true
-select                     float_ops
-output                     stdout:

==================Model Analysis Report======================

Doc:
scope: The nodes in the model graph are organized by 

INFO:tensorflow:Assets written to: /tmp/tmp94vlah65/assets


INFO:tensorflow:Assets written to: /tmp/tmp94vlah65/assets


Epoch 1/500
428/428 [==============================] - 6s 9ms/step - loss: 6.1462 - accuracy: 0.2044 - val_loss: 2.1503 - val_accuracy: 0.2160

Epoch 00001: val_accuracy improved from -inf to 0.21600, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 2/500
428/428 [==============================] - 3s 7ms/step - loss: 1.9806 - accuracy: 0.2815 - val_loss: 1.8839 - val_accuracy: 0.3270

Epoch 00002: val_accuracy improved from 0.21600 to 0.32700, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 3/500
428/428 [==============================] - 3s 7ms/step - loss: 1.7860 - accuracy: 0.3363 - val_loss: 1.8017 - val_accuracy: 0.3460

Epoch 00003: val_accuracy improved from 0.32700 to 0.34600, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 4/500
428/428 [==============================] - 3s 7ms/step - loss: 1.6645 - accuracy: 0.3732 - val_loss: 1.6698 - val_accuracy: 0.3890

Epoch 00004: val_accuracy improved from 0.34600 to 0.38900, saving model to Auritus_noadvNUCLEO_F746ZG.

428/428 [==============================] - 3s 7ms/step - loss: 0.6015 - accuracy: 0.7812 - val_loss: 0.7743 - val_accuracy: 0.7480

Epoch 00036: val_accuracy improved from 0.74700 to 0.74800, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 37/500
428/428 [==============================] - 3s 7ms/step - loss: 0.5889 - accuracy: 0.7859 - val_loss: 0.7853 - val_accuracy: 0.7330

Epoch 00037: val_accuracy did not improve from 0.74800
Epoch 38/500
428/428 [==============================] - 3s 7ms/step - loss: 0.5821 - accuracy: 0.7898 - val_loss: 0.7761 - val_accuracy: 0.7580

Epoch 00038: val_accuracy improved from 0.74800 to 0.75800, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 39/500
428/428 [==============================] - 3s 8ms/step - loss: 0.5632 - accuracy: 0.7980 - val_loss: 0.7771 - val_accuracy: 0.7390

Epoch 00039: val_accuracy did not improve from 0.75800
Epoch 40/500
428/428 [==============================] - 3s 7ms/step - loss: 0.5429 - accuracy: 0.8033 - val

...


Epoch 00318: val_accuracy did not improve from 0.91500
Epoch 319/500
428/428 [==============================] - 4s 9ms/step - loss: 0.0692 - accuracy: 0.9767 - val_loss: 0.4439 - val_accuracy: 0.8990

Epoch 00319: val_accuracy did not improve from 0.91500
Epoch 320/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0583 - accuracy: 0.9823 - val_loss: 0.4893 - val_accuracy: 0.8990

Epoch 00320: val_accuracy did not improve from 0.91500
Epoch 321/500
428/428 [==============================] - 4s 9ms/step - loss: 0.0598 - accuracy: 0.9815 - val_loss: 0.6110 - val_accuracy: 0.9000

Epoch 00321: val_accuracy did not improve from 0.91500
Epoch 322/500
428/428 [==============================] - 4s 9ms/step - loss: 0.0519 - accuracy: 0.9838 - val_loss: 0.4255 - val_accuracy: 0.9020

Epoch 00322: val_accuracy did not improve from 0.91500
Epoch 323/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0690 - accuracy: 0.9776 - val_loss: 0.4344 - val_accuracy: 0.

428/428 [==============================] - 4s 8ms/step - loss: 0.0775 - accuracy: 0.9792 - val_loss: 0.4572 - val_accuracy: 0.8970

Epoch 00359: val_accuracy did not improve from 0.91600
Epoch 360/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0603 - accuracy: 0.9822 - val_loss: 0.4205 - val_accuracy: 0.9030

Epoch 00360: val_accuracy did not improve from 0.91600
Epoch 361/500
428/428 [==============================] - 4s 9ms/step - loss: 0.0536 - accuracy: 0.9837 - val_loss: 0.4313 - val_accuracy: 0.8990

Epoch 00361: val_accuracy did not improve from 0.91600
Epoch 362/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0550 - accuracy: 0.9832 - val_loss: 0.4361 - val_accuracy: 0.9170

Epoch 00362: val_accuracy improved from 0.91600 to 0.91700, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 363/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0532 - accuracy: 0.9849 - val_loss: 0.4195 - val_accuracy: 0.9140

Epoch 00363

428/428 [==============================] - 4s 8ms/step - loss: 0.0729 - accuracy: 0.9791 - val_loss: 0.4506 - val_accuracy: 0.9060

Epoch 00399: val_accuracy did not improve from 0.92500
Epoch 400/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0652 - accuracy: 0.9821 - val_loss: 0.4661 - val_accuracy: 0.9040

Epoch 00400: val_accuracy did not improve from 0.92500
Epoch 401/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0598 - accuracy: 0.9814 - val_loss: 0.4669 - val_accuracy: 0.9010

Epoch 00401: val_accuracy did not improve from 0.92500
Epoch 402/500
428/428 [==============================] - 4s 9ms/step - loss: 0.0584 - accuracy: 0.9824 - val_loss: 0.3962 - val_accuracy: 0.9160

Epoch 00402: val_accuracy did not improve from 0.92500
Epoch 403/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0565 - accuracy: 0.9826 - val_loss: 0.3892 - val_accuracy: 0.9140

Epoch 00403: val_accuracy did not improve from 0.92500
Epoch 404

428/428 [==============================] - 4s 8ms/step - loss: 0.0622 - accuracy: 0.9820 - val_loss: 0.4231 - val_accuracy: 0.9090

Epoch 00440: val_accuracy did not improve from 0.92500
Epoch 441/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0501 - accuracy: 0.9841 - val_loss: 0.4102 - val_accuracy: 0.9080

Epoch 00441: val_accuracy did not improve from 0.92500
Epoch 442/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0490 - accuracy: 0.9847 - val_loss: 0.3943 - val_accuracy: 0.9100

Epoch 00442: val_accuracy did not improve from 0.92500
Epoch 443/500
428/428 [==============================] - 4s 9ms/step - loss: 0.0481 - accuracy: 0.9866 - val_loss: 0.3678 - val_accuracy: 0.9080

Epoch 00443: val_accuracy did not improve from 0.92500
Epoch 444/500
428/428 [==============================] - 4s 9ms/step - loss: 0.0460 - accuracy: 0.9862 - val_loss: 0.3739 - val_accuracy: 0.9080

Epoch 00444: val_accuracy did not improve from 0.92500
Epoch 445

428/428 [==============================] - 4s 8ms/step - loss: 0.0415 - accuracy: 0.9885 - val_loss: 0.4192 - val_accuracy: 0.8970

Epoch 00481: val_accuracy did not improve from 0.92500
Epoch 482/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0496 - accuracy: 0.9859 - val_loss: 0.4386 - val_accuracy: 0.8970

Epoch 00482: val_accuracy did not improve from 0.92500
Epoch 483/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0510 - accuracy: 0.9842 - val_loss: 0.4626 - val_accuracy: 0.9050

Epoch 00483: val_accuracy did not improve from 0.92500
Epoch 484/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0583 - accuracy: 0.9832 - val_loss: 0.4582 - val_accuracy: 0.9050

Epoch 00484: val_accuracy did not improve from 0.92500
Epoch 485/500
428/428 [==============================] - 4s 8ms/step - loss: 0.0469 - accuracy: 0.9852 - val_loss: 0.4575 - val_accuracy: 0.9090

Epoch 00485: val_accuracy did not improve from 0.92500
Epoch 486

# Train the best model

In [8]:
input_dim=X_tr.shape[2]

model = compiled_tcn(return_sequences=False,
                     num_feat=input_dim,
                     num_classes=Y_tr.shape[1],
                     nb_filters=results['best_params']['nb_filters'],
                     kernel_size=results['best_params']['kernel_size'],
                     dilations=results['best_params']['dil_list'],
                     nb_stacks=1,
                     max_len=window_size,
                     use_weight_norm=False,
                     use_skip_connections=results['best_params']['use_skip_connections'])

opt = tf.keras.optimizers.Adam()
model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
              optimizer=opt,metrics=['accuracy'])

checkpoint = ModelCheckpoint(model_name, monitor='val_accuracy', verbose=1, save_best_only=True)
model.fit(x=X_tr, y=Y_tr,validation_data=(X_val,Y_val),
          epochs=model_epochs,callbacks=[checkpoint],shuffle=True,verbose=1)

model = load_model(model_name,custom_objects={'TCN': TCN})
test_accu = model.evaluate(x=X_test,y=Y_test)[1]
print('Test Accuracy:', test_accu)
adv_accu = perform_fgsm_attack(data=X_test, lab=Y_test,eps=epsilon,my_model=model)
print('Adversarial Accuracy:', adv_accu)

x.shape= (None, 14)
model.x = (None, 550, 6)
model.y = (None, 9)
Epoch 1/500
428/428 [==============================] - 3s 7ms/step - loss: 15.1967 - accuracy: 0.1709 - val_loss: 5.1189 - val_accuracy: 0.2700

Epoch 00001: val_accuracy improved from -inf to 0.27000, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 2/500
428/428 [==============================] - 3s 6ms/step - loss: 3.6990 - accuracy: 0.2874 - val_loss: 2.5017 - val_accuracy: 0.3450

Epoch 00002: val_accuracy improved from 0.27000 to 0.34500, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 3/500
428/428 [==============================] - 3s 7ms/step - loss: 2.2387 - accuracy: 0.3547 - val_loss: 1.8568 - val_accuracy: 0.3970

Epoch 00003: val_accuracy improved from 0.34500 to 0.39700, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 4/500
428/428 [==============================] - 3s 7ms/step - loss: 1.8334 - accuracy: 0.3907 - val_loss: 1.6601 - val_accuracy: 0.4370

Epoch 00004: val_accuracy improved fr

428/428 [==============================] - 3s 6ms/step - loss: 0.5794 - accuracy: 0.7751 - val_loss: 0.5432 - val_accuracy: 0.7850

Epoch 00035: val_accuracy did not improve from 0.79800
Epoch 36/500
428/428 [==============================] - 3s 6ms/step - loss: 0.5609 - accuracy: 0.7794 - val_loss: 0.5342 - val_accuracy: 0.7970

Epoch 00036: val_accuracy did not improve from 0.79800
Epoch 37/500
428/428 [==============================] - 3s 6ms/step - loss: 0.5657 - accuracy: 0.7804 - val_loss: 0.5178 - val_accuracy: 0.8290

Epoch 00037: val_accuracy improved from 0.79800 to 0.82900, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 38/500
428/428 [==============================] - 3s 6ms/step - loss: 0.5403 - accuracy: 0.7881 - val_loss: 0.5083 - val_accuracy: 0.8130

Epoch 00038: val_accuracy did not improve from 0.82900
Epoch 39/500
428/428 [==============================] - 3s 6ms/step - loss: 0.5422 - accuracy: 0.7903 - val_loss: 0.5013 - val_accuracy: 0.8110

Epoch 00039: va

428/428 [==============================] - 3s 6ms/step - loss: 0.3670 - accuracy: 0.8548 - val_loss: 0.3965 - val_accuracy: 0.8520

Epoch 00074: val_accuracy did not improve from 0.86400
Epoch 75/500
428/428 [==============================] - 3s 6ms/step - loss: 0.3598 - accuracy: 0.8567 - val_loss: 0.3586 - val_accuracy: 0.8730

Epoch 00075: val_accuracy improved from 0.86400 to 0.87300, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 76/500
428/428 [==============================] - 3s 6ms/step - loss: 0.3729 - accuracy: 0.8527 - val_loss: 0.3636 - val_accuracy: 0.8710

Epoch 00076: val_accuracy did not improve from 0.87300
Epoch 77/500
428/428 [==============================] - 3s 6ms/step - loss: 0.3639 - accuracy: 0.8545 - val_loss: 0.4052 - val_accuracy: 0.8450

Epoch 00077: val_accuracy did not improve from 0.87300
Epoch 78/500
428/428 [==============================] - 3s 6ms/step - loss: 0.3570 - accuracy: 0.8549 - val_loss: 0.3691 - val_accuracy: 0.8560

Epoch 00078: va

428/428 [==============================] - 3s 6ms/step - loss: 0.2894 - accuracy: 0.8841 - val_loss: 0.3542 - val_accuracy: 0.8710

Epoch 00114: val_accuracy did not improve from 0.88100
Epoch 115/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2903 - accuracy: 0.8825 - val_loss: 0.3250 - val_accuracy: 0.8710

Epoch 00115: val_accuracy did not improve from 0.88100
Epoch 116/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2839 - accuracy: 0.8860 - val_loss: 0.3338 - val_accuracy: 0.8740

Epoch 00116: val_accuracy did not improve from 0.88100
Epoch 117/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2879 - accuracy: 0.8840 - val_loss: 0.3140 - val_accuracy: 0.8770

Epoch 00117: val_accuracy did not improve from 0.88100
Epoch 118/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2791 - accuracy: 0.8885 - val_loss: 0.3183 - val_accuracy: 0.8760

Epoch 00118: val_accuracy did not improve from 0.88100
Epoch 119

428/428 [==============================] - 3s 6ms/step - loss: 0.2607 - accuracy: 0.9042 - val_loss: 0.3107 - val_accuracy: 0.9000

Epoch 00154: val_accuracy improved from 0.89900 to 0.90000, saving model to Auritus_noadvNUCLEO_F746ZG.hdf5
Epoch 155/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2472 - accuracy: 0.9021 - val_loss: 0.3102 - val_accuracy: 0.8890

Epoch 00155: val_accuracy did not improve from 0.90000
Epoch 156/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2544 - accuracy: 0.9024 - val_loss: 0.3299 - val_accuracy: 0.8790

Epoch 00156: val_accuracy did not improve from 0.90000
Epoch 157/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2479 - accuracy: 0.9048 - val_loss: 0.2817 - val_accuracy: 0.8990

Epoch 00157: val_accuracy did not improve from 0.90000
Epoch 158/500
428/428 [==============================] - 3s 6ms/step - loss: 0.2407 - accuracy: 0.9049 - val_loss: 0.2750 - val_accuracy: 0.9020

Epoch 00158

...

428/428 [==============================] - 3s 6ms/step - loss: 0.1837 - accuracy: 0.9363 - val_loss: 0.2480 - val_accuracy: 0.9250

Epoch 00394: val_accuracy did not improve from 0.93400
Epoch 395/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1736 - accuracy: 0.9394 - val_loss: 0.2319 - val_accuracy: 0.9220

Epoch 00395: val_accuracy did not improve from 0.93400
Epoch 396/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1677 - accuracy: 0.9414 - val_loss: 0.2082 - val_accuracy: 0.9270

Epoch 00396: val_accuracy did not improve from 0.93400
Epoch 397/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1703 - accuracy: 0.9399 - val_loss: 0.2142 - val_accuracy: 0.9280

Epoch 00397: val_accuracy did not improve from 0.93400
Epoch 398/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1780 - accuracy: 0.9387 - val_loss: 0.2479 - val_accuracy: 0.9180

Epoch 00398: val_accuracy did not improve from 0.93400
Epoch 399

428/428 [==============================] - 3s 7ms/step - loss: 0.1567 - accuracy: 0.9446 - val_loss: 0.2285 - val_accuracy: 0.9180

Epoch 00435: val_accuracy did not improve from 0.93400
Epoch 436/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1706 - accuracy: 0.9404 - val_loss: 0.2613 - val_accuracy: 0.9180

Epoch 00436: val_accuracy did not improve from 0.93400
Epoch 437/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1688 - accuracy: 0.9403 - val_loss: 0.2240 - val_accuracy: 0.9260

Epoch 00437: val_accuracy did not improve from 0.93400
Epoch 438/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1707 - accuracy: 0.9430 - val_loss: 0.2238 - val_accuracy: 0.9260

Epoch 00438: val_accuracy did not improve from 0.93400
Epoch 439/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1679 - accuracy: 0.9420 - val_loss: 0.2364 - val_accuracy: 0.9190

Epoch 00439: val_accuracy did not improve from 0.93400
Epoch 440

428/428 [==============================] - 3s 7ms/step - loss: 0.1551 - accuracy: 0.9459 - val_loss: 0.2134 - val_accuracy: 0.9240

Epoch 00476: val_accuracy did not improve from 0.93400
Epoch 477/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1474 - accuracy: 0.9464 - val_loss: 0.2580 - val_accuracy: 0.9250

Epoch 00477: val_accuracy did not improve from 0.93400
Epoch 478/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1713 - accuracy: 0.9403 - val_loss: 0.2386 - val_accuracy: 0.9180

Epoch 00478: val_accuracy did not improve from 0.93400
Epoch 479/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1625 - accuracy: 0.9436 - val_loss: 0.2500 - val_accuracy: 0.9170

Epoch 00479: val_accuracy did not improve from 0.93400
Epoch 480/500
428/428 [==============================] - 3s 6ms/step - loss: 0.1697 - accuracy: 0.9404 - val_loss: 0.2171 - val_accuracy: 0.9230

Epoch 00480: val_accuracy did not improve from 0.93400
Epoch 481

100%|█████████████████████████████████████████| 300/300 [00:18<00:00, 16.04it/s]

Adversarial Accuracy: 0.2
